# Libraries, data

In [36]:
import pandas as pd
import spacy
from spacy import displacy
from spacy.matcher import Matcher

In [37]:
import warnings
warnings.filterwarnings('ignore')

In [38]:
# Import English library
nlp = spacy.load('en_core_web_lg')

In [39]:
dfWater=pd.read_json("dfwaterpub.json")[["title","abstract"]]

# Pattern for propositional attitudes "we [VERB]"

https://spacy.io/usage/rule-based-matching

https://explosion.ai/demos/matcher?

In [40]:
dfWater=dfWater.dropna(subset=["abstract"])

In [41]:
dfWater["doc"]=dfWater["abstract"].apply(nlp)

In [42]:
df=dfWater
a=df.iloc[2].abstract
exemplar=nlp(a)

In [43]:
allsentences=[]
for i in range (2000):
    a=df.iloc[i].abstract
    b=nlp(a)
    for s in b.sents:
        allsentences.append(s)

In [44]:
type(allsentences[0])

spacy.tokens.span.Span

In [45]:
len(allsentences)

15212

In [46]:
allsentences.append("test test")

In [47]:
len(allsentences)

15213

# Propositional research attitudes

- GOAL (intention, goal):  
    - aim, seek, study, undertake, investigate, intend
- DISCOV: 
    - show, propose, obtain, report, observe, create, demonstrate, detect, scrutinize, provide

## training data

- prepare matching function for sentences, output in format JSONL

In [48]:
verbtags={"GOAL":
       ["aim","seek","study","undertake","investigate","intend"],
       "DISCOV":
        ["show","provide","notice","report"]
         }

In [49]:
def actionverb(abstract):
    matches=matcher(abstract)
    listDisc=[]
    for _,start,end in matches:
        verb=abstract[end-1].text
        verblem=abstract[end-1].lemma_
        for ent,verbs in verbtags.items():
            if verblem in verbs:
                dict_disc=(start+1,end,ent)
                listDisc.append(dict_disc)
    return(listDisc)

In [50]:
dfWater["discNER"]=dfWater["doc"].apply(actionverb)  

NameError: name 'matcher' is not defined

In [51]:
dfWater.head(19)

title  \
0     Integrating an hourly weather generator with a...   
1     Synthesizing existing frameworks to identify t...   
10          Water Treatment: Are Membranes the Panacea?   
100   Water scarcity and fish imperilment driven by ...   
1000  Reconstructing pre-instrumental streamflow in ...   
1001  The causes and impacts of water resources cris...   
1002  Impacts of Near‐Term Climate Change on Irrigat...   
1003  Analysis of the relationship between rainfall ...   
1004  Evaluation of Water Security in Kathmandu Vall...   
1005  Water Security as Shared Security Challenges? ...   
1006  Seasonal patterns and socio-economic predictor...   
1007  Evaluating the Hydrologic Performance of Low I...   
1008  Conceptual framework to ensure water security ...   
1009  Editorial: Special Issue on Water security and...   
101   Development of spatial decision-making for gro...   
1010  Energy implications of the millennium drought ...   
1011  Water impacts and water-climate goal conflicts...   
1012  Access to water and morbidity in children in t...   
1013  Freshwater vulnerability under high end climat...   

                                               abstract  \
0      The Ru River Basin is facing severe water sec...   
1      Imbalance between water supply and demand is ...   
10    Alongside the rising global water demand, cont...   
100   Human consumption of freshwater is now approac...   
1000   Streamflow reconstructions based on paleoclim...   
1001   Owing to its combination of superior natural ...   
1002  Adaptation to a changing climate is critical t...   
1003   The relationship between rainfall variability...   
1004  Kathmandu Upatyaka Khanepani Limited (KUKL) ha...   
1005  This article analyses the water security probl...   
1006  Seasonal water insecurity is a growing concern...   
1007  As urbanization progresses, increasingly imper...   
1008  &lt;p&gt;<strong>Abstract.</strong> As a resul...   
1009                                                      
101   Assessment of groundwater conditions particula...   
1010  Abstract During the Millennium Drought in Aust...   
1011  &lt;p&gt;<strong>Abstract.</strong> To meet bo...   
1012  BACKGROUND: Water insecurity is an important r...   
1013  As freshwater availability is crucial for secu...   

                                                    doc  
0     ( , The, Ru, River, Basin, is, facing, severe,...  
1     ( , Imbalance, between, water, supply, and, de...  
10    (Alongside, the, rising, global, water, demand...  
100   (Human, consumption, of, freshwater, is, now, ...  
1000  ( , Streamflow, reconstructions, based, on, pa...  
1001  ( , Owing, to, its, combination, of, superior,...  
1002  (Adaptation, to, a, changing, climate, is, cri...  
1003  ( , The, relationship, between, rainfall, vari...  
1004  (Kathmandu, Upatyaka, Khanepani, Limited, (, K...  
1005  (This, article, analyses, the, water, security...  
1006  (Seasonal, water, insecurity, is, a, growing, ...  
1007  (As, urbanization, progresses, ,, increasingly...  
1008  (&, lt;p&gt;<strong, >, Abstract.</strong, >, ...  
1009                                                 ()  
101   (Assessment, of, groundwater, conditions, part...  
1010  (Abstract, During, the, Millennium, Drought, i...  
1011  (&, lt;p&gt;<strong, >, Abstract.</strong, >, ...  
1012  (BACKGROUND, :, Water, insecurity, is, an, imp...  
1013  (As, freshwater, availability, is, crucial, fo...

# Causal hypothesis

In [52]:
allsentences

[ The Ru River Basin is facing severe water security challenges such as frequent occurrence of extreme events and serious nutrient enrichment of its water bodies.,
 In simulating daily streamflow, monthly total nitrogen (TN) loads, and monthly total phosphorous (TP) loads of the basin, the SWAT (Soil and Water Assessment Tool) model utilizing hourly rainfall inputs was found to perform considerably better than the model utilizing daily rainfall inputs.,
 For climate change impact assessment, the hourly weather generator AWE-GEN was calibrated based on historical hourly rainfall records from 1970 to 1999 in the basin.,
 Evaluation of its performance have indicated that the AWE-GEN could reasonably characterize the main features of monthly, daily, and hourly rainfall in the basin.,
 The outputs of eight GCMs under a total of four climate change scenarios were then downscaled with the AWE-GEN to produce synthetic future hourly rainfall series to drive the hourly rainfall SWAT model for cl

In [53]:
for sent in allsentences:
    print(f"*****\nfor {sent}")
    chunks=list(sent.noun_chunks)
    print("noun chunks:",chunks)

*****
for  The Ru River Basin is facing severe water security challenges such as frequent occurrence of extreme events and serious nutrient enrichment of its water bodies.
noun chunks: [ The Ru River Basin, severe water security challenges, frequent occurrence, extreme events, serious nutrient enrichment, its water bodies]
*****
for In simulating daily streamflow, monthly total nitrogen (TN) loads, and monthly total phosphorous (TP) loads of the basin, the SWAT (Soil and Water Assessment Tool) model utilizing hourly rainfall inputs was found to perform considerably better than the model utilizing daily rainfall inputs.
noun chunks: [daily streamflow, monthly total phosphorous, TP) loads, the basin, the SWAT (Soil and Water Assessment Tool) model, hourly rainfall inputs, the model, daily rainfall inputs]
*****
for For climate change impact assessment, the hourly weather generator AWE-GEN was calibrated based on historical hourly rainfall records from 1970 to 1999 in the basin.
noun chun

for Decreasing of DP load mainly aggregated in the western and eastern mountainous regions, while it tended to increase in the northern and middle regions.
noun chunks: [DP load, the western and eastern mountainous regions, it, the northern and middle regions]
*****
for This study was expected to provide insights into diffuse nutrient loss control and management in Xin&#x27;anjiang catchment, and scientific references for the implementation of water environmental protection in China.
noun chunks: [This study, insights, diffuse nutrient loss control, management, Xin&#x27;anjiang catchment, scientific references, the implementation, water environmental protection, China]
*****
for U.S. military and allied contingency operations are increasingly occurring in locations with limited, unstable or compromised fresh water supplies.
noun chunks: [U.S. military and allied contingency operations, locations, fresh water supplies]
*****
for Non-potable graywater reuse is currently under assessment 

for Some events of 2015 have politically legitimised climate change and its mitigation, and 2016 saw the world finally sworn to action.
noun chunks: [Some events, politically legitimised climate change, its mitigation, the world, action]
*****
for The bioeconomy holds some of the answers to the economic challenges thrown up by mitigating climate change while maintaining growth and societal wellbeing.
noun chunks: [The bioeconomy, the answers, the economic challenges, climate change, growth, societal wellbeing]
*****
for For bioeconomy policy makers, the future is complex and multi-faceted.
noun chunks: [bioeconomy policy makers, the future]
*****
for The issues start in regions and extend to global reach.
noun chunks: [The issues, regions, global reach]
*****
for It is hard to quantify what is going to be the most difficult of challenges.
noun chunks: [It, what, challenges]
*****
for However, one of the visions for the bioeconomy, that of distributed manufacturing in small- and medium-

noun chunks: [the final section, we, the ethical transition, built environment professions]
*****
for LESSONS LEARNT:
noun chunks: []
*****
for Built environment interventions must move beyond simple ecological sustainability to encouraging ways of life that are healthy for both humans and the planet.
noun chunks: [Built environment interventions, simple ecological sustainability, ways, life, both humans, the planet]
*****
for There are key challenges facing this new approach.
noun chunks: [key challenges, this new approach]
*****
for In a 2013 report released by the United Nations water insecurity was identified as a national security issue.
noun chunks: [a 2013 report, the United Nations water insecurity, a national security issue]
*****
for This is due to the close correlation between mismanagement of water resources and acute conflict.
noun chunks: [the close correlation, mismanagement, water resources, acute conflict]
*****
for With humanity&#x27;s available potable water table un

noun chunks: [Part II, the research topic, “Connecting Mountain Hydroclimate, the American Cordilleras, the hydroclimate variability, the Andes, the sub-continental scale, the effects, El Niño-Southern Oscillation]
*****
for The objective of water policy making should be to address problems related to water such as water scarcity, water pollution, and droughts and floods in a manner that the resource is able to perform all its three functions, namely, social good, economic good, and environmental good.
noun chunks: [The objective, water policy making, problems, water, water scarcity, water pollution, droughts, floods, a manner, the resource, all its three functions, namely, social good, economic good, environmental good]
*****
for The countries of sub-Saharan Africa score very low on water security, affecting food production and water use for domestic and livestock sector adversely with an overall impact on the economy.
noun chunks: [The countries, sub-Saharan Africa, water security, f

...

for Over a billion people around the world lack access to safe drinking water and over two billion have little or no sanitation.
noun chunks: [Over a billion people, the world, access, safe drinking water, little or no sanitation]
*****
for Do we have the resources — and the will — to provide the water to support a booming population?
noun chunks: [we, the resources, the will, the water, a booming population]
*****
for This issue of Nature (see introduction, p. 269 and Editorial,
noun chunks: [This issue, Nature, introduction, p., Editorial]
*****
for p. 253) tackles the science, economics and politics of the global water crisis.
noun chunks: [p., the science, economics, politics, the global water crisis]
*****
for Climate scientists say that unreliable rains and drier summer soils will become more common:
noun chunks: [Climate scientists, unreliable rains, drier summer soils]
*****
for Quirin Schiermeier reports on water strategies for a drier world.
noun chunks: [Quirin Schiermeier, 

*****
for Changes in the surface energy balance, hydrologic cycle, and carbon budget feedback to regional and global weather and climate systems.
noun chunks: [Changes, the surface energy balance, hydrologic cycle, carbon budget feedback, regional and global weather and climate systems]
*****
for Two-thirds of the Northern Hemisphere high latitude land mass resides in Northern Eurasia (~20% of the global land mass), and this region has undergone  sweeping socio-economic change throughout the 20th century.
noun chunks: [Two-thirds, the Northern Hemisphere high latitude land mass, Northern Eurasia, the global land mass, this region, socio-economic change, the 20th century]
*****
for How this carbon-rich, cold region component of the Earth system functions as a regional entity and interacts with and feeds back to the greater global system is to a large extent unknown.
noun chunks: [this carbon-rich, cold region component, the Earth system functions, a regional entity, the greater global s

noun chunks: [analytical evidence, the potential effects, return waters, the quality, the Amu Darya river, the paper reports, comments, data, salinity and metals contents, the waters, the artificial channel network, Bukhara, the Amu Darya river, Bukhara, the dam, the Tuyamuyn Hydro Complex (THC]
*****
for METHODS:
noun chunks: [METHODS]
*****
for A total of 15 sampling sites were selected for the analytical survey: Two sites were located on the Amu Darya river downstream from the inflow of the return waters from Bukhara, two in the river entering in the THC, and three downstream from the dam forming the reservoir complex.
noun chunks: [A total, 15 sampling sites, the analytical survey, Two sites, the Amu Darya river, the inflow, the return waters, Bukhara, the river, the THC, the dam, the reservoir complex]
*****
for The waters entering and leaving the Bukhara agricultural area were sampled in two main collectors, while the waters flowing in the channel system were sampled in six disti

noun chunks: [This paper, the solutions, such a term, any hydrological or economic rationale, increased abstraction]
*****
for If this conclusion is correct, water resource planners need to reconsider arguments that the water crisis is inevitable in the search for water and food security.
noun chunks: [this conclusion, water resource planners, arguments, the water crisis, the search, water and food security]
*****
for This article discusses how water utilities are struggling with determining what the appropriate security improvements should be at each individual facility, now that the deadline for submittal of their vulnerability assessments has come and gone.
noun chunks: [This article, water utilities, what, the appropriate security improvements, each individual facility, the deadline, submittal, their vulnerability assessments]
*****
for The article focuses on areas where federal government help is needed, that include: providing more detailed threat information; cost benefit analys

AttributeError: 'str' object has no attribute 'noun_chunks'

In [ ]:
# similarity to key expression. Here "MERS infection"

In [54]:
newlist=[]
key_term="insecurity"
for sent in allsentences:
    chunks=list(sent.noun_chunks)
    for noun in chunks:
        sim=noun.similarity(nlp(key_term))
        newlist.append([sim, noun])
        print(f"{noun} #### ähnlich: {sim}")

TypeError: append() takes exactly one argument (2 given)

In [22]:
type(allsentences[0])

spacy.tokens.span.Span

In [56]:
key_term="insecurity"
for sent in allsentences:
    chunks=list(sent.noun_chunks)
    for noun in chunks:
        sim=noun.similarity(nlp(key_term))
        print(f"{noun} #### ähnlich: {sim}")

 The Ru River Basin #### ähnlich: 0.07661174640297724
severe water security challenges #### ähnlich: 0.4452790136453154
frequent occurrence #### ähnlich: 0.31361839398678265
extreme events #### ähnlich: 0.3044183944787608
serious nutrient enrichment #### ähnlich: 0.34875336195214723
its water bodies #### ähnlich: 0.20897159241732344
daily streamflow #### ähnlich: 0.16078231131113793
monthly total phosphorous #### ähnlich: 0.195571205106895
TP) loads #### ähnlich: -0.0178481301840243
the basin #### ähnlich: 0.17079481947230135
the SWAT (Soil and Water Assessment Tool) model #### ähnlich: 0.22235882410761107
hourly rainfall inputs #### ähnlich: 0.23930977835730655
the model #### ähnlich: 0.1470154318380437
daily rainfall inputs #### ähnlich: 0.2614632052580842
climate change impact assessment #### ähnlich: 0.36445624405623617
the hourly weather generator #### ähnlich: 0.1898387489411847
AWE-GEN #### ähnlich: 0.167278231878813
historical hourly rainfall records #### ähnlich: 0.21040421755

river dewatering #### ähnlich: 0.06742065118126477
ways #### ähnlich: 0.2693442538799953
them #### ähnlich: 0.19367723318977412
We #### ähnlich: 0.1916828458065046
irrigation #### ähnlich: 0.1506055928216833
cattle-feed crops #### ähnlich: 0.2597929447685381
the greatest consumer #### ähnlich: 0.2866556436385677
river water #### ähnlich: 0.08168434004184
the western United States #### ähnlich: 0.2512092397161412
beef and dairy consumption #### ähnlich: 0.2725428908726557
the leading driver #### ähnlich: 0.18018323990576443
water shortages #### ähnlich: 0.36745729346976375
fish imperilment #### ähnlich: 0.08112848606181744
the region #### ähnlich: 0.25203722424211156
We #### ähnlich: 0.1916828458065046
opportunities #### ähnlich: 0.23928773954452648
water scarcity #### ähnlich: 0.41963844167578634
cattle-feed production #### ähnlich: 0.2046364839182003
temporary, rotational fallowing #### ähnlich: 0.23388521088015657
irrigated feed crops #### ähnlich: 0.2703325638061123
water shortage r

Adaptation #### ähnlich: 0.17629840978527267
a changing climate #### ähnlich: 0.32049452132677547
future global food and water security challenges #### ähnlich: 0.39228242172911865
these challenges #### ähnlich: 0.3522512934108419
successful adaptation strategies #### ähnlich: 0.22392927254101855
regional scales #### ähnlich: 0.25770448532596546
regional‐scale studies #### ähnlich: 0.16208115383950364
adaptation decision making #### ähnlich: 0.21451444448442622
climate change #### ähnlich: 0.35383298742994473
both water supply #### ähnlich: 0.19484826371782302
demand #### ähnlich: 0.32292909310776574
water demand #### ähnlich: 0.24666764720660697
regional scales #### ähnlich: 0.25770448532596546
The goal #### ähnlich: 0.17163336282233957
this work #### ähnlich: 0.2296545775012812
this gap #### ähnlich: 0.3209103916501678
the direct impacts #### ähnlich: 0.30026535748488836
near‐term #### ähnlich: 0.0
the 2030s #### ähnlich: 0.13854944794496574
climate change #### ähnlich: 0.35383298742

the end #### ähnlich: 0.18624025634714933
170 MLD #### ähnlich: 0.002919016291707875
million liters #### ähnlich: 0.06956578764986227
the first phase #### ähnlich: 0.1462604004527897
an additional 340 MLD #### ähnlich: 0.10505535410322951
the second phase #### ähnlich: 0.15246169842512508
The area #### ähnlich: 0.19026430004011827
a severe water deficit #### ähnlich: 0.3533836551054422
existing infrastructure #### ähnlich: 0.2637196105333344
a limited capability #### ähnlich: 0.21537887576029754
only 19% #### ähnlich: 0.06937810102630036
the water #### ähnlich: 0.1534127144530132
its service areas #### ähnlich: 0.20602097052800536
the dry season #### ähnlich: 0.15717767231117388
the wet season #### ähnlich: 0.14196837453847932
this context #### ähnlich: 0.31695918357590336
this study #### ähnlich: 0.22155723966132612
the temporal trends #### ähnlich: 0.31403073277327054
spatial distribution #### ähnlich: 0.2407171528014366
household water security index #### ähnlich: 0.2900354598714569

19.5% #### ähnlich: -0.005676837590550252
the EcoPerf scenario #### ähnlich: 0.27977234267735673
the costs #### ähnlich: 0.24869900519243907
104% #### ähnlich: -0.04621246746819009
83.6% #### ähnlich: 0.04060430046644698
The reduction rates #### ähnlich: 0.24748595767414805
four pollutants #### ähnlich: 0.1425739139830661
TSS #### ähnlich: 0.028469346561173354
TP #### ähnlich: -0.07146419676986082
COD #### ähnlich: 0.04961154341373212
the MaxPerf scenario #### ähnlich: 0.27977234267735673
59.8-61.1% #### ähnlich: -0.014122994522737627
SpoPerf #### ähnlich: 0.0
53.9-58.3% #### ähnlich: -0.028046238145805775
EcoPerf #### ähnlich: 0.0
42.3-45.4% #### ähnlich: -0.006699824847009195
the costs #### ähnlich: 0.24869900519243907
the three scenarios #### ähnlich: 0.20423776986953598
1.83 million yuan #### ähnlich: 0.07712901980020548
These results #### ähnlich: 0.1956298689159377
guidance #### ähnlich: 0.1796216430355236
urban stormwater managers #### ähnlich: 0.2752328798492138
future urban pl

...

the temporal dimension #### ähnlich: 0.2710684295667996
We #### ähnlich: 0.1916828458065046
a UWSS model #### ähnlich: 0.12317150257271449
Guizhou province #### ähnlich: 0.17109498072374377
China #### ähnlich: 0.06022299014965417
influencing factors #### ähnlich: 0.3679404174792731
main driving factors #### ähnlich: 0.2966354958852064
system variation law #### ähnlich: 0.23428446337381947
the SD method #### ähnlich: 0.10699520798427858
We #### ähnlich: 0.1916828458065046
the water security system #### ähnlich: 0.26741384891311243
four scenarios #### ähnlich: 0.17742728888516146
(Guiyang scenario #### ähnlich: 0.17981349666347862
Zunyi scenario #### ähnlich: 0.2803603336806075
Bijie scenario #### ähnlich: 0.2803603336806075
combined scenario #### ähnlich: 0.2861855761063488
The results #### ähnlich: 0.17524734098744268
(1) the severity #### ähnlich: 0.13909338940403077
water security #### ähnlich: 0.28200169761034694
cities #### ähnlich: 0.19414376149048168
three cities #### ähnlich: 0.

water source conservation #### ähnlich: 0.18560774954455503
risk control measures #### ähnlich: 0.3483345999886552
order #### ähnlich: 0.09860106334463503
the security #### ähnlich: 0.32488453867453354
drinking water #### ähnlich: 0.1618341157224089
This paper #### ähnlich: 0.1627582293712189
relevant strategic suggestions #### ähnlich: 0.2048867115389368
the security #### ähnlich: 0.32488453867453354
drinking water #### ähnlich: 0.1618341157224089
Shanshan County #### ähnlich: 0.070433176583531
equipment #### ähnlich: 0.04170486829099626
the project #### ähnlich: 0.17419451640316372
the system #### ähnlich: 0.19038211863149196
devices #### ähnlich: 0.09596313232084383
instrumentation #### ähnlich: 0.05665611523983199
the management system #### ähnlich: 0.22246626538263473
an intelligent water management platform #### ähnlich: 0.1872053813851213
This study #### ähnlich: 0.22155723966132612
a reference #### ähnlich: 0.11449510592557317
problems #### ähnlich: 0.41545060100006226
drinking

human capabilities #### ähnlich: 0.2990502383167286
sociocultural dynamics #### ähnlich: 0.3296664938129748
political institutions #### ähnlich: 0.35985558458456696
processes #### ähnlich: 0.18463303880396298
This paper #### ähnlich: 0.1627582293712189
a mix #### ähnlich: 0.13468061214643315
qualitative and quantitative methods #### ähnlich: 0.2202661496431251
cultural, geographic, and demographic contexts #### ähnlich: 0.3605142035172299
measure #### ähnlich: 0.18584638599049288
household water insecurity #### ähnlich: 0.6294783679002394
it #### ähnlich: 0.2386880668230982
existing methods #### ähnlich: 0.1649958132346895
household water insecurity #### ähnlich: 0.6294783679002394
ways #### ähnlich: 0.2693442538799953
methodological innovations #### ähnlich: 0.2636219317236793
a broader definition #### ähnlich: 0.27296384029226606
household water insecurity #### ähnlich: 0.6294783679002394
groundwater #### ähnlich: 0.21545541863393905
the largest store #### ähnlich: 0.1056980444273936

the drivers #### ähnlich: 0.19688715576202923
barriers #### ähnlich: 0.3849794012154975
their implementation #### ähnlich: 0.26031406229499493
the assessments #### ähnlich: 0.2399087785813226
it #### ähnlich: 0.2386880668230982
the implementation #### ähnlich: 0.2064610812242601
the actual cost #### ähnlich: 0.2176045848069758
water #### ähnlich: 0.10563803786021439
AED10.32/m3 #### ähnlich: 0.0
water consumption #### ähnlich: 0.21292157226988223
expats #### ähnlich: 0.21857613686638325
5.4% #### ähnlich: 0.000882885421450398
Significant reduction #### ähnlich: 0.289406570925533
water consumption #### ähnlich: 0.21292157226988223
locals #### ähnlich: 0.17895588157312134
Domestic water savings #### ähnlich: 0.246508135860344
up to 19.8% #### ähnlich: 0.1079071648760097
water-efficient household fixtures #### ähnlich: 0.11715116007426299
Irrigation #### ähnlich: 0.1506055928216833
complete wastewater reuse #### ähnlich: 0.08416615334149867
water leakage #### ähnlich: 0.19258812648166
10%

KeyboardInterrupt: 

In [81]:
import warnings
warnings.filterwarnings('ignore')
newlist=[]
key_term="water security"
for sent in allsentences[:1000]:
    chunks=list(sent.noun_chunks)
    for noun in chunks:
        sim=noun.similarity(nlp(key_term))
        if (sim > 0.7):
            if [sim, str(noun)] not in newlist:
                newlist.append([sim, str(noun)])
newlist.sort(key=lambda x:x[0])
for i in newlist:
    print(i)

[0.7000828331676919, 'virtual water trade']
[0.7001100435226618, 'The ‘water user']
[0.7001869327202542, 'drinking water']
[0.7002187959370152, 'the rising global water demand']
[0.7011608227050515, 'river water content reductions']
[0.7012950142881489, 'The water-food nexus']
[0.7013649917868451, 'sustainable water']
[0.7020745857433013, 'the water resources safety relative closeness degree']
[0.7026370233165379, 'sustainable water resources management']
[0.7027832135678458, 'a national security issue']
[0.7030156655614164, 'sustainable water quality management']
[0.7034707971446781, 'all major water-using sectors']
[0.7041651538873467, 'regional water resources']
[0.7051619752317745, 'water scarcity problems']
[0.7052346291063111, 'water influence']
[0.7054414933240036, 'drinking water sources']
[0.7057876223906666, 'water bodies']
[0.706974368509281, 'international security']
[0.7074179244039472, 'higher water availability']
[0.7077245715804211, 'The water and energy cycles']
[0.707

In [78]:
str(newlist[2][1])

'food, energy and water security'

In [76]:
sim[:2]

IndexError: invalid index to scalar variable.

In [23]:
import warnings
warnings.filterwarnings('ignore')
newlist=[]
key_term="water security"
for sent in allsentences[:1000]:
    chunks=list(sent.noun_chunks)
    for noun in chunks:
        sim=noun.similarity(nlp(key_term))
        if (sim > 0.5):
            newlist.append([sim, noun])
newlist.sort(key=lambda x:x[0])
print(newlist)

In [24]:
type(sent)

str

In [25]:
key_term="insecurity"
def similar_nchunks(doc,keyterm,cumlist,threshhold=0.5):
    key=nlp(keyterm)
    chunks=list(doc.noun_chunks)
    for noun in chunks:
        simval=noun.similarity(key)
        if simval>threshhold:
            cumlist.append((noun,simval))
    return(cumlist)

In [26]:
cumlist

NameError: name 'cumlist' is not defined

In [27]:
similar_nchunks(exemplar,"water security",[])

[(the rising global water demand, 0.7002187959370152),
 (current water supplies, 0.7420947936474533),
 (nontraditional source waters, 0.532197815456561),
 (domestic needs, 0.5712370850096237),
 (water security, 1.0),
 (increasingly complex waters, 0.5900075310048803),
 (The technical feasibility, 0.5129440557442552),
 (alternative water supplies, 0.7166473977228265),
 ((e.g., wastewater, 0.5089978848961058),
 (produced water, 0.6422877472990975),
 (typical and emerging water quality goals, 0.6633821583554108),
 (the effectiveness, 0.5294285406128721),
 (these water quality goals, 0.6487631153114733),
 (the future, 0.5056190796219768),
 (water treatment, 0.6995236503067189),
 (energy conservation, 0.5401852799562069)]

In [28]:
cumlist=[]
dfWater["doc"].apply(lambda x:similar_nchunks(x,"water security",cumlist))
cumlist

[( The Ru River Basin, 0.5038631443725973),
 (severe water security challenges, 0.8465667486963725),
 (its water bodies, 0.7096385528205574),
 (the basin, 0.5280127385963699),
 (the SWAT (Soil and Water Assessment Tool) model, 0.6941674918731985),
 (climate change impact assessment, 0.558991232307789),
 (the hourly weather generator, 0.5646808439927287),
 (the basin, 0.5280127385963699),
 (the basin, 0.5280127385963699),
 (a total of four climate change scenarios, 0.5783051879675822),
 (synthetic future hourly rainfall series, 0.5068040925182773),
 (the hourly rainfall SWAT model, 0.5222303878312028),
 (climate change impact assessment, 0.558991232307789),
 (the flood season, 0.523206039546378),
 (the Ru River Basin, 0.5038632135107239),
 (climate change, 0.5046950442408754),
 (the enforcement, 0.5817181434737295),
 (additional nutrient abatement measures, 0.5435001186607519),
 (the adverse impacts, 0.5015235036027323),
 (climate change, 0.5046950442408754),
 (water supply, 0.763246714

In [ ]:
cumlist=[]
dfWater["doc"].apply(lambda x:similar_nchunks(x,"water security",cumlist,threshhold=0.7))
for i in cumlist:
    if 

In [ ]:
key_term="insecurity"
def similar_nchunks(doc,keyterm,cumlist,threshhold=0.5):
    key=nlp(keyterm)
    chunks=list(doc.noun_chunks)
    for noun in chunks:
        simval=noun.similarity(key)
        if simval>threshhold:
            cumlist.append((noun,simval))
    return(cumlist)

In [34]:
newlist=[]
key_term="insecurity"
for sent in allsentences:
    chunks=list(sent.noun_chunks)
    for noun in chunks:
        sim=noun.similarity(nlp(key_term))
        if sim > 0.5:
            newlist.append([sim, noun])
print(newlist)

AttributeError: 'str' object has no attribute 'noun_chunks'

In [35]:
type(sent)

str